In [1]:
%reset -f

import pandas as pd
import numpy
import time
from sklearn.neural_network import MLPClassifier
from imblearn.pipeline import Pipeline
from imblearn.pipeline import Pipeline as imbpipeline

from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import StratifiedKFold
from sklearn.preprocessing import StandardScaler, MinMaxScaler
from sklearn.feature_selection import SelectKBest, chi2, f_classif
from imblearn.over_sampling import SMOTE
from sklearn.metrics import confusion_matrix
from sklearn.metrics import balanced_accuracy_score
from sklearn.metrics import classification_report
from sklearn.metrics import fbeta_score
from sklearn.metrics import make_scorer
import pandas as pd
import numpy
import time
from sklearn.metrics import confusion_matrix
from sklearn.metrics import balanced_accuracy_score

import time
import pandas as pd
import os.path
import os
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.pyplot as plt
import cv2 
from sklearn.metrics import mean_squared_log_error
from matplotlib import pyplot as plt
from PIL import Image
from IPython.display import Image, display
import tensorflow
os.environ['PATH'] += ';C:\\Program Files\\Graphviz\\bin'
import graphviz
from IPython.display import Image
from keras.utils.vis_utils import plot_model
from tensorflow.keras.callbacks import EarlyStopping, ModelCheckpoint
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import StandardScaler, MinMaxScaler
from keras.wrappers.scikit_learn import KerasRegressor



from sklearn.model_selection import KFold

from keras.wrappers.scikit_learn import KerasClassifier
from sklearn.model_selection import cross_val_score

!pip install talos
import talos


def RMSLE(y_true, y_pred):
    return np.sqrt(mean_squared_log_error(y_true, y_pred))

Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com
/usr/share/python-wheels/urllib3-1.25.8-py2.py3-none-any.whl/urllib3/connectionpool.py:999: InsecureRequestWarning: Unverified HTTPS request is being made to host 'pypi.ngc.nvidia.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
     |████████████████████████████████| 55 kB 3.8 MB/s eta 0:00:011
/usr/share/python-wheels/urllib3-1.25.8-py2.py3-none-any.whl/urllib3/connectionpool.py:999: InsecureRequestWarning: Unverified HTTPS request is being made to host 'pypi.ngc.nvidia.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#ssl-warnings
/usr/share/python-wheels/urllib3-1.25.8-py2.py3-none-any.whl/urllib3/connectionpool.py:999: InsecureRequestWarning: Unverified HTTPS request is being made to host 'pypi.ngc.nvidia.com'. Adding certificate verification is st

In [2]:
environment_variables = dir()

In [3]:
# Input parameters
TRAINING_FILES = ["../data/original/training_dataset.csv"]
EVALUATION_FILES = ["../data/original/evaluation_dataset.csv"]

FILE_N = 0
INPUT_TRAINING_FILE = TRAINING_FILES[FILE_N] 
INPUT_EVALUATION_FILE = EVALUATION_FILES[FILE_N]


# Output parameters
METHOD_NAME = "keras_tensorflow_resnet"
TIMESTAMP = time.strftime("%d_%m_%Y-%H_%M_%S")
OUTPUT_MODEL_FOLDER = f"../data/models/keras_models"
OUTPUT_MODEL = f"../data/models/{METHOD_NAME}_keras_model_{TIMESTAMP}.pkl"
OUTPUT_RESULTS = f"../data/results/{METHOD_NAME}_model_{TIMESTAMP}.txt"
OUTPUT_MODEL_ARCHITECTURE_RESULTS = f"../img/{METHOD_NAME}_model_{TIMESTAMP}.png"

# Hyper parameter alternatives
# Bankrupt companies must have higher weight, because there are fewer samples

# Hyper parameter optimization parameters
HYPER_PARAMETER_OPTIMIZATION_SCORING = "accuracy"
HYPER_PARAMETER_OPTIMIZATION_CV = 5

# Cross validation parameters
CROSS_VALIDATION_CV = 5

# Cost parameters
PUNISHMENT_FOR_FALSE_BANKRUPT_PREDICTION = 100

# Other constants
LABELS = ["Operational", "Bankrupt"]
RANDOM_SEED = 42

# Hyper parameter alternatives
HYPER_PARAMETER_HIDDEN_LAYER_SIZES = [(100,)]
HYPER_PARAMETER_K_FEATURES = list([20,25,30,35,40,95])
HYPER_PARAMETER_SCORE_FUNC = [chi2, f_classif]
HYPER_PARAMETER_CLASIFIER_OPTIMIZERS = ['rmsprop','adam','adagrad']
HYPER_PARAMETER_EPOCHS = [20]
HYPER_PARAMETER_DROPUT = [0,0.2]
HYPER_PARAMETER_LAYERS_N = list(range(20,90,10))
HYPER_PARAMETER_BATCH_NUMBER = list(range(20,90,30))
HYPER_PARAMETER_KERNEL_INITIALIZER = ['glorot_uniform','normal','uniform']
HYPER_PARAMETER_CLASIFIER_METRICS = ['accuracy']
HYPER_PARAMETER_ALPHA = list(10.0 ** -numpy.arange(1, 7))

# Hyper parameter optimization parameters
HYPER_PARAMETER_OPTIMIZATION_BETA = 2
HYPER_PARAMETER_OPTIMIZATION_CV = 5



In [4]:

training_dataset = pd.read_csv(INPUT_TRAINING_FILE, engine="python", delimiter=",")
training_features = training_dataset.loc[:, training_dataset.columns != "Bankrupt?"]
training_targets = training_dataset["Bankrupt?"]

evaluation_dataset = pd.read_csv(INPUT_EVALUATION_FILE, engine="python", delimiter=",")
evaluation_features = evaluation_dataset.loc[:, evaluation_dataset.columns != "Bankrupt?"]
evaluation_targets = evaluation_dataset["Bankrupt?"]

training_dataset.head()

Bankrupt?   ROA(C) before interest and depreciation before interest  \
0          0                                           0.328621          
1          0                                           0.529128          
2          0                                           0.502218          
3          0                                           0.486082          
4          0                                           0.522400          

    ROA(A) before interest and % after tax  \
0                                 0.286088   
1                                 0.546991   
2                                 0.564054   
3                                 0.545083   
4                                 0.577519   

    ROA(B) before interest and depreciation after tax  \
0                                           0.343487    
1                                           0.572675    
2                                           0.567750    
3                                           0.537877    
4                                           0.563574    

    Operating Gross Margin   Realized Sales Gross Margin  \
0                 0.543183                      0.543183   
1                 0.613651                      0.613637   
2                 0.627474                      0.627474   
3                 0.604873                      0.604844   
4                 0.610113                      0.610192   

    Operating Profit Rate   Pre-tax net Interest Rate  \
0                0.997320                    0.795251   
1                0.999090                    0.797475   
2                0.999006                    0.797438   
3                0.998997                    0.797412   
4                0.999094                    0.797564   

    After-tax net Interest Rate   Non-industry income and expenditure/revenue  \
0                      0.807303                                      0.303237   
1                      0.809396                                      0.303420   
2                      0.809428                                      0.303533   
3                      0.809330                                      0.303505   
4                      0.809432                                      0.303567   

   ...   Net Income to Total Assets   Total assets to GNP price  \
0  ...                     0.631838                    0.000809   
1  ...                     0.804139                    0.089456   
2  ...                     0.813615                    0.000215   
3  ...                     0.801497                    0.002832   
4  ...                     0.819700                    0.007407   

    No-credit Interval   Gross Profit to Sales  \
0             0.623315                0.543178   
1             0.623503                0.613651   
2             0.623942                0.627473   
3             0.623702                0.604872   
4             0.623851                0.610110   

    Net Income to Stockholder's Equity   Liability to Equity  \
0                             0.823296              0.282771   
1                             0.840650              0.278799   
2                             0.841078              0.276533   
3                             0.840925              0.291015   
4                             0.842184              0.281070   

    Degree of Financial Leverage (DFL)  \
0                             0.026763   
1                             0.026929   
2                             0.026850   
3                             0.027270   
4                             0.026818   

    Interest Coverage Ratio (Interest expense to EBIT)   Net Income Flag  \
0                                           0.565019                   1   
1                                           0.565739                   1   
2                                           0.565424                   1   
3                                           0.566729                   1   
4                        

In [5]:

def keras_model_for_sklearn(optimizer='adam',#'adagrad',
                    loss = 'binary_crossentropy', 
                    kernel_initializer='glorot_uniform', 
                    dropout=0.2, layers_n  = 95,
                    n_activator = 'relu',
                    neurons = 213 ,
                    n_out = 1,
                    f_activator = 'relu',
                    batch_norm = True,
                    metrics = ['accuracy', 'MeanSquaredError', 'AUC', "RootMeanSquaredError"]
                  ):
        
    
    input =tensorflow.keras.layers.Input(shape=(layers_n,))
    output1 =tensorflow.keras.layers.Dense(layers_n, input_shape=(layers_n,), activation=n_activator)(input)
    if batch_norm:
        output1 =tensorflow.keras.layers.BatchNormalization(axis=1, name='dense_relu' + '2a')(output1)
    output1 =tensorflow.keras.layers.Dropout(dropout)(output1)
    dense_name_base = "dense"
    bn_name_base = "dense_additionall"
    shortcut1 =tensorflow.keras.layers.Dense(layers_n, activation=n_activator, kernel_initializer='he_normal',
                                name=dense_name_base + '1')(output1)
    output1 =tensorflow.keras.layers.Dropout(dropout)(output1)

    # if batch_norm:
    #     output1 =tensorflow.keras.layers.BatchNormalization(axis=1, name=bn_name_base + '2a')(output1)
    # shortcut2 =tensorflow.keras.layers.Dense(neurons, activation=n_activator, kernel_initializer='he_normal',
    #                             name=dense_name_base + '2')(output1)
    
    # output1 =tensorflow.keras.layers.Dropout(dropout)(output1)
    # shortcut1 =tensorflow.keras.layers.Dense(neurons, activation=n_activator, kernel_initializer='he_normal',
    #                             name=dense_name_base + '22')(output1)
    
    output1 =tensorflow.keras.layers.Dropout(dropout)(output1)
    output =tensorflow.keras.layers.Dense(n_out, activation=f_activator, name='fc1000')(output1)
    
    # Final model
    model =tensorflow.keras.models.Model(inputs=input, outputs=output)

    # Plot model information
    # plot_= True
    # # plot_model(model, to_file=OUTPUT_MODEL_ARCHITECTURE_RESULTS, show_shapes=True, show_layer_names=True)
    # if plot_:
    #     plot_model(model, to_file=OUTPUT_MODEL_ARCHITECTURE_RESULTS, show_shapes=True, show_layer_names=True)
    #     im = cv2.imread(OUTPUT_MODEL_ARCHITECTURE_RESULTS, 0)
    #     model.summary()
    #     display(Image(filename=OUTPUT_MODEL_ARCHITECTURE_RESULTS))

    model.compile(loss=loss, optimizer=optimizer, metrics=metrics)

    return model
print(type(keras_model_for_sklearn()))# <class 'keras.engine.functional.Functional'>


<class 'keras.engine.functional.Functional'>


2022-05-18 19:59:24.543253: E tensorflow/stream_executor/cuda/cuda_driver.cc:271] failed call to cuInit: CUDA_ERROR_COMPAT_NOT_SUPPORTED_ON_DEVICE: forward compatibility was attempted on non supported HW
2022-05-18 19:59:24.543312: I tensorflow/stream_executor/cuda/cuda_diagnostics.cc:169] retrieving CUDA diagnostic information for host: ignas-MS-7B09
2022-05-18 19:59:24.543324: I tensorflow/stream_executor/cuda/cuda_diagnostics.cc:176] hostname: ignas-MS-7B09
2022-05-18 19:59:24.543569: I tensorflow/stream_executor/cuda/cuda_diagnostics.cc:200] libcuda reported version is: 470.129.6
2022-05-18 19:59:24.543626: I tensorflow/stream_executor/cuda/cuda_diagnostics.cc:204] kernel reported version is: 470.103.1
2022-05-18 19:59:24.543644: E tensorflow/stream_executor/cuda/cuda_diagnostics.cc:313] kernel version 470.103.1 does not match DSO version 470.129.6 -- cannot find working devices in this configuration
2022-05-18 19:59:24.544163: I tensorflow/core/platform/cpu_feature_guard.cc:151] T

### Creating Keras model 

In [6]:
import numpy as np

from sklearn.linear_model import LogisticRegression
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import GridSearchCV
from keras.layers import Dense, Dropout,     BatchNormalization, SeparableConv2D, MaxPooling2D, Activation, Flatten
from keras.models import Model, Sequential
from keras.wrappers.scikit_learn import KerasRegressor
from sklearn.metrics import confusion_matrix, classification_report, roc_curve, fbeta_score, make_scorer

from sklearn.metrics import recall_score, f1_score, roc_auc_score, accuracy_score, precision_score, precision_recall_curve, average_precision_score



In [10]:
from keras.layers import Input, Dense, Add

# create a function that returns a model, taking as parameters things you
# want to verify using cross-valdiation and model selection
def create_model(optimizer='adam', kernel_initializer='normal', dropout=0.2, layers_n = 64, metrics="accuracy", batchn = True, hidden_layer_sizes = [20,90]):
    model = Sequential()
    
    model.add(Dense(layers_n,activation='relu',kernel_initializer=kernel_initializer))
    model.add(Dropout(dropout))
    if batchn:
        model.add(BatchNormalization())
    model.add(Dense(1,activation='relu',kernel_initializer=kernel_initializer))
    model.compile(loss='binary_crossentropy',optimizer=optimizer, metrics=[metrics])
    return model
print(type(create_model())) # <class 'keras.engine.sequential.Sequential'>


param_grid = {
    "selection__k": HYPER_PARAMETER_K_FEATURES,
    "selection__score_func": HYPER_PARAMETER_SCORE_FUNC,
    'clf__optimizer':HYPER_PARAMETER_CLASIFIER_OPTIMIZERS,
    'clf__epochs':HYPER_PARAMETER_EPOCHS,
    'clf__dropout':HYPER_PARAMETER_DROPUT,
    'clf__layers_n' : HYPER_PARAMETER_LAYERS_N,
    # 'clf__batchn' : HYPER_PARAMETER_BATCH_NUMBER,
    'clf__kernel_initializer':HYPER_PARAMETER_KERNEL_INITIALIZER,
    'clf__metrics':HYPER_PARAMETER_CLASIFIER_METRICS,
}


# param_grid = {
#     'clf__optimizer':['adam'],
#     'clf__epochs':[10],
#     'clf__dropout':[0.2],
#     'clf__layers_n' : [64],
#     'clf__kernel_initializer':['uniform'],
#     'clf__metrics':['accuracy'],
#     "selection__k": [30],
#     "selection__score_func": [chi2],
# }


# Using keras regresor for our custom model
clf = KerasRegressor(build_fn=create_model,verbose=3)

# Definng standart scalers
scaler = StandardScaler()

# Do feature selection with SelectKBest.
feature_selection = SelectKBest(f_classif,  k=64)  

# Oversample data with SMOTE
smote = SMOTE(sampling_strategy="minority", random_state=RANDOM_SEED)
X_train, y_train = training_features,training_targets
X_train, y_train = smote.fit_resample(training_features,training_targets)
# Min max scaler definition 
min_max_scaler =  MinMaxScaler()

# Feature selection 
feature_selection = SelectKBest()

pipeline = Pipeline([
    ('preprocess',scaler),
    ("min_max_scaler", min_max_scaler),
    ("selection", feature_selection),
    ('clf',clf)
])

# Define custom fbeta scorer function that put emphasis on recall
def custom_scorer(y_true, y_pred):
    confidence = 0
    y_pred = (np.where(y_pred > confidence, 1, 0))    
    print(confusion_matrix(y_true, y_pred))
    return fbeta_score(y_true, y_pred, beta=HYPER_PARAMETER_OPTIMIZATION_BETA)

grid = GridSearchCV(pipeline, 
                            cv=5,
                            param_grid=param_grid
                            , verbose = 3 
                            , scoring=make_scorer(custom_scorer)
                            )

grid.fit(X_train, y_train)


<class 'keras.engine.sequential.Sequential'>
Fitting 5 folds for each of 1512 candidates, totalling 7560 fits
Epoch 1/20
Epoch 2/20
Epoch 3/20
Epoch 4/20
Epoch 5/20
Epoch 6/20
Epoch 7/20
Epoch 8/20
Epoch 9/20
Epoch 10/20
Epoch 11/20
Epoch 12/20
Epoch 13/20
Epoch 14/20
Epoch 15/20
Epoch 16/20
Epoch 17/20
Epoch 18/20
Epoch 19/20
Epoch 20/20
[[1331  781]
 [   0    0]]
[CV 1/5] END clf__dropout=0, clf__epochs=20, clf__kernel_initializer=glorot_uniform, clf__layers_n=20, clf__metrics=accuracy, clf__optimizer=rmsprop, selection__k=20, selection__score_func=<function chi2 at 0x7f0efc34b040>;, score=0.000 total time=   6.4s
Epoch 1/20
Epoch 2/20
Epoch 3/20
Epoch 4/20
Epoch 5/20
Epoch 6/20
Epoch 7/20
Epoch 8/20
Epoch 9/20
Epoch 10/20
Epoch 11/20
Epoch 12/20
Epoch 13/20
Epoch 14/20
Epoch 15/20
Epoch 16/20
Epoch 17/20
Epoch 18/20
Epoch 19/20
Epoch 20/20
[[1426  686]
 [   0    0]]
[CV 2/5] END clf__dropout=0, clf__epochs=20, clf__kernel_initializer=glorot_uniform, clf__layers_n=20, clf__metrics=ac

GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('preprocess', StandardScaler()),
                                       ('min_max_scaler', MinMaxScaler()),
                                       ('selection', SelectKBest()),
                                       ('clf',
                                        <keras.wrappers.scikit_learn.KerasRegressor object at 0x7f0fb5770e80>)]),
             param_grid={'clf__dropout': [0, 0.2], 'clf__epochs': [20],
                         'clf__kernel_initializer': ['glorot_uniform', 'normal',
                                                     'uniform'],
                         'clf__layers_n': [20, 30, 40, 50, 60, 70, 80],
                         'clf__metrics': ['accuracy'],
                         'clf__optimizer': ['rmsprop', 'adam', 'adagrad'],
                         'selection__k': [20, 25, 30, 35, 40, 95],
                         'selection__score_func': [<function chi2 at 0x7f0efc34b040>,
                              

## Best score and model parameters

- F-Beta (2) score = 0.592773

In [11]:
print("Best model: Acc. Score = %f, with parameters %s" % (grid.best_score_, grid.best_params_))

Best model: Acc. Score = 0.592773, with parameters {'clf__dropout': 0, 'clf__epochs': 20, 'clf__kernel_initializer': 'normal', 'clf__layers_n': 80, 'clf__metrics': 'accuracy', 'clf__optimizer': 'rmsprop', 'selection__k': 35, 'selection__score_func': <function chi2 at 0x7f0efc34b040>}


## For single class

In [12]:
def output_parameters(confidence, grid, training_features, training_targets,evaluation_features, evaluation_targets, max_acc,best_conf, log = False ):
    from sklearn.metrics import confusion_matrix, classification_report, roc_curve, recall_score, make_scorer

    # Use all training data to calculate confusion matrix for training data
    training_estimates_ = grid.predict(training_features)
    training_estimates = np.where(training_estimates_ > confidence, 1, 0)

    training_accuracy = balanced_accuracy_score(training_targets, training_estimates)
    training_confusion_matrix = confusion_matrix(training_targets, training_estimates)

    # Use model to estimate manually labeled evaluation Tweets
    evaluation_estimates_ = grid.predict(evaluation_features)

    evaluation_estimates = np.where(evaluation_estimates_ > confidence, 1, 0)

    evaluation_accuracy = balanced_accuracy_score(evaluation_targets, evaluation_estimates)
    evaluation_confusion_matrix = confusion_matrix(evaluation_targets, evaluation_estimates)
    
    # evaluation_confusion_matrix = confusion_matrix_to_string(evaluation_confusion_matrix)
    if max_acc <= evaluation_accuracy:
        max_acc = evaluation_accuracy
        best_conf = confidence

    print(f"Confidence {confidence}")
    if log:
        print(training_estimates_)
        print("\n\n\n\n\n\n_________________________________________________")
        print(training_estimates)
        print(training_confusion_matrix)
        print(evaluation_estimates_[:5])
        print(evaluation_estimates[:5])
        print(evaluation_confusion_matrix)

    print(f"Balanced training. acc: {training_accuracy}")

    print(f"Balanced eval. acc: {evaluation_accuracy}")

    # summarize results

    if log:
        print("Best: %f using %s" % (grid.best_score_, grid.best_params_))
        means = grid.cv_results_['mean_test_score']
        stds = grid.cv_results_['std_test_score']
        params = grid.cv_results_['params']
        for mean, stdev, param in zip(means, stds, params):
            print("%f (%f) with: %r" % (mean, stdev, param))

        print("Training evaluation")

        y_pred_train_ = grid.predict(training_features)
        print(y_pred_train_)
        y_pred_train = np.where(y_pred_train_ > confidence, 1, 0)
        print(classification_report(training_targets, y_pred_train))
        train_conf_matrix = confusion_matrix(training_targets, y_pred_train)

        print("Validation/evaluation")
        y_pred_test_ = grid.predict(evaluation_features) # prediction on our test set

        print(y_pred_test_)
        y_pred_test = np.where(y_pred_test_ > confidence, 1, 0)

        print(classification_report(evaluation_targets, y_pred_test))
        test_conf_matrix = confusion_matrix(evaluation_targets, y_pred_test)
        print(test_conf_matrix)
    return max_acc, best_conf

confidences =  numpy.arange(0, 1,0.02)
max_acc = 0
best_conf = 0
log = False

for confidence in confidences:
    max_acc,best_conf = output_parameters(confidence, grid, training_features, training_targets,evaluation_features, evaluation_targets, max_acc,best_conf, log = False )

print(f"max_acc {max_acc}, best_conf{best_conf}")

Confidence 0.0
Balanced training. acc: 0.9136264616232412
Balanced eval. acc: 0.7943181818181818
Confidence 0.02
Balanced training. acc: 0.9123957059704835
Balanced eval. acc: 0.7954545454545454
Confidence 0.04
Balanced training. acc: 0.9146688637655203
Balanced eval. acc: 0.7984848484848486
Confidence 0.06
Balanced training. acc: 0.9104077692056003
Balanced eval. acc: 0.7996212121212121
Confidence 0.08
Balanced training. acc: 0.9065255342781864
Balanced eval. acc: 0.8011363636363636
Confidence 0.1
Balanced training. acc: 0.9088934069813498
Balanced eval. acc: 0.8026515151515152
Confidence 0.12
Balanced training. acc: 0.9086098004098573
Balanced eval. acc: 0.7950757575757575
Confidence 0.14
Balanced training. acc: 0.9105988134805145
Balanced eval. acc: 0.7969696969696969
Confidence 0.16
Balanced training. acc: 0.9032126651053058
Balanced eval. acc: 0.7882575757575758
Confidence 0.18
Balanced training. acc: 0.9019819094525479
Balanced eval. acc: 0.7890151515151516
Confidence 0.2
Balance

In [13]:
confidence = best_conf
max_acc,best_conf = output_parameters(best_conf, grid, training_features, training_targets,evaluation_features, evaluation_targets, max_acc,best_conf, log = True )


Confidence 0.1
[1.2960249  0.         0.         ... 1.0611836  0.38974482 0.06794833]






_________________________________________________
[1 0 0 ... 1 1 0]
[[4827  452]
 [  17  159]]
[0.        0.5353547 0.        0.        0.       ]
[0 1 0 0 0]
[[1189  131]
 [  13   31]]
Balanced training. acc: 0.9088934069813498
Balanced eval. acc: 0.8026515151515152
Best: 0.592773 using {'clf__dropout': 0, 'clf__epochs': 20, 'clf__kernel_initializer': 'normal', 'clf__layers_n': 80, 'clf__metrics': 'accuracy', 'clf__optimizer': 'rmsprop', 'selection__k': 35, 'selection__score_func': <function chi2 at 0x7f0efc34b040>}
0.583240 (0.476663) with: {'clf__dropout': 0, 'clf__epochs': 20, 'clf__kernel_initializer': 'glorot_uniform', 'clf__layers_n': 20, 'clf__metrics': 'accuracy', 'clf__optimizer': 'rmsprop', 'selection__k': 20, 'selection__score_func': <function chi2 at 0x7f0efc34b040>}
0.581673 (0.475738) with: {'clf__dropout': 0, 'clf__epochs': 20, 'clf__kernel_initializer': 'glorot_uniform', 'clf__

In [14]:
current_variables = dir()

results_string = ""

for variable in current_variables:
    # Skip environment variables and their container variable
    # Ignore also underscore variables
    if variable in environment_variables or variable == "environment_variables" or variable.startswith("_"):
        continue

    # Get variables value
    variable_value = globals()[variable]

    # If variable is numerical or string, append it to results
    if type(variable_value) is str or type(variable_value) is int or \
        type(variable_value) is float or type(variable_value) is list or \
        type(variable_value) is numpy.float64 or type(variable_value) is dict:
        results_string += f"{variable}: {variable_value}\n"

# Print results to screen
print(results_string)

# Save results to file
with open(OUTPUT_RESULTS, "w") as file:
    file.write(results_string)

CROSS_VALIDATION_CV: 5
EVALUATION_FILES: ['../data/original/evaluation_dataset.csv', '..\\data\\preprocessed\\difference_preprocessed_evaluation_dataset.csv', '..\\data\\preprocessed\\ole_RemoveOutliers_and_preprocessing_pipe_evaluation_dataset.csv']
FILE_N: 0
HYPER_PARAMETER_ALPHA: [0.1, 0.01, 0.001, 0.0001, 1e-05, 1e-06]
HYPER_PARAMETER_BATCH_NUMBER: [20, 50, 80]
HYPER_PARAMETER_CLASIFIER_METRICS: ['accuracy']
HYPER_PARAMETER_CLASIFIER_OPTIMIZERS: ['rmsprop', 'adam', 'adagrad']
HYPER_PARAMETER_DROPUT: [0, 0.2]
HYPER_PARAMETER_EPOCHS: [20]
HYPER_PARAMETER_HIDDEN_LAYER_SIZES: [(100,)]
HYPER_PARAMETER_KERNEL_INITIALIZER: ['glorot_uniform', 'normal', 'uniform']
HYPER_PARAMETER_K_FEATURES: [20, 25, 30, 35, 40, 95]
HYPER_PARAMETER_LAYERS_N: [20, 30, 40, 50, 60, 70, 80]
HYPER_PARAMETER_OPTIMIZATION_BETA: 2
HYPER_PARAMETER_OPTIMIZATION_CV: 5
HYPER_PARAMETER_OPTIMIZATION_SCORING: accuracy
HYPER_PARAMETER_SCORE_FUNC: [<function chi2 at 0x7f0efc34b040>, <function f_classif at 0x7f0efc33cee0>]
I

In [15]:
# !pip install import weakref

import pickle


with open(OUTPUT_MODEL, "wb") as handle:
    joblib.dump(grid, OUTPUT_MODEL)


NameError: name 'joblib' is not defined